# Information Security Lab - Experiments 1 to 7
**Generated from Lab Manual**

This notebook contains the exact code logic from the lab manual for experiments 1 through 7.

In [ ]:
# Install required library for Experiments 2, 3, 6, 7
!pip install pycryptodome

## Experiment 1 - Implement Classical Encryption Techniques

In [ ]:
# --- CAESAR CIPHER ---
def encrypt_caesar(text, shift):
    result = ""
    for char in text:
        if char.isalpha():
            base = ord('A') if char.isupper() else ord('a')
            result += chr((ord(char) - base + shift) % 26 + base)
        else:
            result += char
    return result

def decrypt_caesar(cipher, shift):
    return encrypt_caesar(cipher, -shift)

# Driver Code
print("--- Caesar Cipher ---")
text = input("Enter plaintext: ")
shift = int(input("Enter shift value: "))
ciphertext = encrypt_caesar(text, shift)
print("Encrypted:", ciphertext)
plaintext = decrypt_caesar(ciphertext, shift)
print("Decrypted:", plaintext)

In [ ]:
# --- PLAYFAIR CIPHER ---
def generate_key_matrix(key):
    key = key.upper().replace("J", "I")
    matrix = []
    used = set()
    for ch in key:
        if ch.isalpha() and ch not in used:
            used.add(ch)
            matrix.append(ch)
    for ch in "ABCDEFGHIKLMNOPQRSTUVWXYZ":
        if ch not in used:
            matrix.append(ch)
    return [matrix[i:i+5] for i in range(0, 25, 5)]

def prepare_text(text):
    text = text.upper().replace("J", "I")
    result = ""
    i = 0
    while i < len(text):
        result += text[i]
        if i + 1 < len(text):
            if text[i] == text[i+1]:
                result += "X"
                i += 1
            else:
                result += text[i+1]
                i += 2
        else:
            i += 1
    if len(result) % 2 != 0:
        result += "X"
    return result

def find_position(matrix, ch):
    for r in range(5):
        for c in range(5):
            if matrix[r][c] == ch:
                return r, c

def playfair_encrypt(text, matrix):
    text = prepare_text(text)
    cipher = ""
    for i in range(0, len(text), 2):
        r1, c1 = find_position(matrix, text[i])
        r2, c2 = find_position(matrix, text[i+1])
        if r1 == r2:
            cipher += matrix[r1][(c1+1)%5]
            cipher += matrix[r2][(c2+1)%5]
        elif c1 == c2:
            cipher += matrix[(r1+1)%5][c1]
            cipher += matrix[(r2+1)%5][c2]
        else:
            cipher += matrix[r1][c2]
            cipher += matrix[r2][c1]
    return cipher

def playfair_decrypt(text, matrix):
    plain = ""
    for i in range(0, len(text), 2):
        r1, c1 = find_position(matrix, text[i])
        r2, c2 = find_position(matrix, text[i+1])
        if r1 == r2:
            plain += matrix[r1][(c1-1)%5]
            plain += matrix[r2][(c2-1)%5]
        elif c1 == c2:
            plain += matrix[(r1-1)%5][c1]
            plain += matrix[(r2-1)%5][c2]
        else:
            plain += matrix[r1][c2]
            plain += matrix[r2][c1]
    return plain.replace("X", "")

# Driver Code
print("--- Playfair Cipher ---")
key = input("Enter key for Playfair: ")
plaintext = input("Enter plaintext: ")
matrix = generate_key_matrix(key)
print("Key Matrix:")
for row in matrix:
    print(" ".join(row))
encrypted = playfair_encrypt(plaintext, matrix)
decrypted = playfair_decrypt(encrypted, matrix)
print("Encrypted:", encrypted)
print("Decrypted:", decrypted)

In [ ]:
# --- VIGENERE CIPHER ---
def generate_key(text, key):
    key = key.upper()
    return (key * (len(text)//len(key)+1))[:len(text)]

def encrypt_vigenere(text, key):
    cipher = ""
    for t, k in zip(text.upper(), key):
        cipher += chr((ord(t)+ord(k))%26+65)
    return cipher

def decrypt_vigenere(cipher, key):
    plain = ""
    for c, k in zip(cipher, key):
        plain += chr((ord(c)-ord(k)+26)%26+65)
    return plain

# Driver Code
print("--- Vigenere Cipher ---")
text = input("Enter plaintext: ").upper()
key = input("Enter key: ").upper()
full_key = generate_key(text, key)
cipher = encrypt_vigenere(text, full_key)
print("Encrypted:", cipher)
print("Decrypted:", decrypt_vigenere(cipher, full_key))

In [ ]:
# --- HILL CIPHER ---
def mod26(x):
    return x % 26

def encrypt_hill(text, key):
    text = "".join([c for c in text.upper() if c.isalpha()])
    if len(text) % 2 != 0:
        text += "X"
    cipher = ""
    for i in range(0, len(text), 2):
        x = ord(text[i]) - 65
        y = ord(text[i+1]) - 65
        c1 = mod26(key[0][0]*x + key[0][1]*y)
        c2 = mod26(key[1][0]*x + key[1][1]*y)
        cipher += chr(c1+65) + chr(c2+65)
    return cipher

# Driver Code
print("--- Hill Cipher ---")
text = input("Enter plaintext: ")
print("Enter key matrix values (4 integers for 2x2 matrix):")
a,b,c,d = map(int, input().split())
key = [[a,b],[c,d]]
cipher = encrypt_hill(text, key)
print("Encrypted:", cipher)

## Experiment 2 - Implement DES and AES

In [ ]:
# --- DES IMPLEMENTATION ---
from Crypto.Cipher import DES
from Crypto.Util.Padding import pad, unpad

def des_encrypt(plaintext, key):
    key = key.encode("utf-8")
    # 8-byte key
    cipher = DES.new(key, DES.MODE_ECB)
    padded_text = pad(plaintext.encode(), DES.block_size)
    encrypted = cipher.encrypt(padded_text)
    return encrypted.hex()

def des_decrypt(cipher_hex, key):
    key = key.encode("utf-8")
    cipher = DES.new(key, DES.MODE_ECB)
    decrypted = cipher.decrypt(bytes.fromhex(cipher_hex))
    try:
        return unpad(decrypted, DES.block_size).decode()
    except:
        return "Padding/Key Error"

print("=== DES Encryption & Decryption ===")
print("NOTE: Key must be exactly 8 characters")
plaintext = input("Enter plaintext: ")
key = input("Enter 8-character key: ")
encrypted_des = des_encrypt(plaintext, key)
print("Encrypted (hex):", encrypted_des)
decrypted_des = des_decrypt(encrypted_des, key)
print("Decrypted:", decrypted_des)

In [ ]:
# --- AES IMPLEMENTATION ---
from Crypto.Cipher import AES
from Crypto.Util.Padding import pad, unpad
from Crypto.Random import get_random_bytes

def aes_encrypt(plaintext, key, mode):
    key = key.ljust(32)[:32].encode() # 256-bit key
    iv = get_random_bytes(16)
    if mode == "ECB":
        cipher = AES.new(key, AES.MODE_ECB)
        encrypted = cipher.encrypt(pad(plaintext.encode(), 16))
        return encrypted.hex(), None
    elif mode == "CBC":
        cipher = AES.new(key, AES.MODE_CBC, iv)
        encrypted = cipher.encrypt(pad(plaintext.encode(), 16))
        return encrypted.hex(), iv.hex()
    elif mode == "CFB":
        cipher = AES.new(key, AES.MODE_CFB, iv)
        encrypted = cipher.encrypt(plaintext.encode())
        return encrypted.hex(), iv.hex()

def aes_decrypt(cipher_hex, key, mode, iv_hex=None):
    key = key.ljust(32)[:32].encode()
    encrypted = bytes.fromhex(cipher_hex)
    if mode == "ECB":
        cipher = AES.new(key, AES.MODE_ECB)
        return unpad(cipher.decrypt(encrypted), 16).decode()
    elif mode == "CBC":
        iv = bytes.fromhex(iv_hex)
        cipher = AES.new(key, AES.MODE_CBC, iv)
        return unpad(cipher.decrypt(encrypted), 16).decode()
    elif mode == "CFB":
        iv = bytes.fromhex(iv_hex)
        cipher = AES.new(key, AES.MODE_CFB, iv)
        return cipher.decrypt(encrypted).decode()

print("\n AES Encryption (ECB/CBC/CFB) ")
plaintext = input("Enter plaintext: ")
key = input("Enter key (max 32 chars): ")
mode = input("Enter mode (ECB/CBC/CFB): ").upper()

encrypted_aes, iv = aes_encrypt(plaintext, key, mode)
print("Encrypted (hex):", encrypted_aes)
if iv:
    print("IV (hex):", iv)

if iv:
    decrypted_aes = aes_decrypt(encrypted_aes, key, mode, iv)
else:
    decrypted_aes = aes_decrypt(encrypted_aes, key, mode)
print("Decrypted:", decrypted_aes)

## Experiment 3 - Implement Blowfish Algorithm

In [ ]:
import time
import base64
from Crypto.Cipher import Blowfish, AES, DES
from Crypto.Util.Padding import pad, unpad

def b64e(b):
    return base64.b64encode(b).decode()

def b64d(s):
    return base64.b64decode(s)

def blowfish_encrypt(message, key):
    cipher = Blowfish.new(key, Blowfish.MODE_ECB)
    ct = cipher.encrypt(pad(message.encode(), Blowfish.block_size))
    return b64e(ct)

def blowfish_decrypt(cipher_b64, key):
    cipher = Blowfish.new(key, Blowfish.MODE_ECB)
    pt = unpad(cipher.decrypt(b64d(cipher_b64)), Blowfish.block_size)
    return pt.decode()

def aes_encrypt_perf(message, key):
    key = key[:16].ljust(16, b'0') # AES requires 16 bytes
    cipher = AES.new(key, AES.MODE_ECB)
    ct = cipher.encrypt(pad(message.encode(), 16))
    return ct

def des_encrypt_perf(message, key):
    key = key[:8].ljust(8, b'0') # DES requires 8 bytes
    cipher = DES.new(key, DES.MODE_ECB)
    ct = cipher.encrypt(pad(message.encode(), 8))
    return ct

def compare_performance(message, iterations=1000):
    bf_key = b"BLOWFISHKEY"
    aes_key = b"AESDEMO123456789"
    des_key = b"DES_KEY!"
    
    # Warm up
    blowfish_encrypt(message, bf_key)
    aes_encrypt_perf(message, aes_key)
    des_encrypt_perf(message, des_key)
    
    t1 = time.time()
    for _ in range(iterations):
        blowfish_encrypt(message, bf_key)
    t2 = time.time()
    
    t3 = time.time()
    for _ in range(iterations):
        aes_encrypt_perf(message, aes_key)
    t4 = time.time()
    
    t5 = time.time()
    for _ in range(iterations):
        des_encrypt_perf(message, des_key)
    t6 = time.time()
    
    print("\n Performance Comparison (ECB) ")
    print(f"Blowfish Encrypt: {(t2-t1)/iterations * 1e6:.2f} µs")
    print(f"AES Encrypt: {(t4-t3)/iterations * 1e6:.2f} µs")
    print(f"DES Encrypt: {(t6-t5)/iterations * 1e6:.2f} µs")

if __name__ == "__main__":
    message = "HELLO BLOWFISH"
    key = b"BLOWFISHKEY"
    
    print("\n--- Blowfish Encryption ---")
    ciphertext = blowfish_encrypt(message, key)
    print("Ciphertext:", ciphertext)
    
    print("\n--- Blowfish Decryption ---")
    plaintext = blowfish_decrypt(ciphertext, key)
    print("Plaintext:", plaintext)
    
    compare_performance("HELLO BLOWFISH", 500)

## Experiment 4 - Key Generation and Distribution

In [ ]:
import secrets
import hashlib

p = int(input("Enter prime p: "))
g = int(input("Enter generator g: "))

a = int(input("Enter Person A private key: "))
b = int(input("Enter Person B private key: "))

A = pow(g, a, p)
B = pow(g, b, p)

S_a = pow(B, a, p)
S_b = pow(A, b, p)

key_a = hashlib.sha256(str(S_a).encode()).hexdigest()
key_b = hashlib.sha256(str(S_b).encode()).hexdigest()

random_session_key = secrets.token_hex(16)

print("\np =", p)
print("g =", g)
print("Person A_private =", a)
print("Person B_private =", b)
print("Person A_public =", A)
print("Person B_public =", B)
print("Shared secret A =", S_a)
print("Shared secret B =", S_b)
print("Derived_session_key_A (hex) =", key_a)
print("Derived_session_key_B (hex) =", key_b)
print("Session_keys_equal =", key_a == key_b)
print("Random_session_key (hex) =", random_session_key)

## Experiment 5 - Implement RSA Algorithm

In [ ]:
import math

def gcd(a, b):
    while b != 0:
        a, b = b, a % b
    return a

def mod_inverse(e, phi):
    for d in range(1, phi):
        if (d * e) % phi == 1:
            return d
    return None

def is_prime(num):
    if num < 2:
        return False
    for i in range(2, int(math.sqrt(num)) + 1):
        if num % i == 0:
            return False
    return True

def generate_keys(p, q):
    if not (is_prime(p) and is_prime(q)):
        raise ValueError("p and q must be prime")
    if p == q:
        raise ValueError("p and q must be different")
    
    n = p * q
    phi = (p - 1) * (q - 1)
    
    e = 2
    while e < phi:
        if gcd(e, phi) == 1:
            break
        e += 1
        
    d = mod_inverse(e, phi)
    return (e, n), (d, n)

def encrypt(message, public_key):
    e, n = public_key
    cipher = [pow(ord(ch), e, n) for ch in message]
    return cipher

def decrypt(cipher, private_key):
    d, n = private_key
    message = [chr(pow(ch, d, n)) for ch in cipher]
    return "".join(message)

print("RSA Algorithm - Encryption and Decryption")
p = int(input("Enter prime number p: "))
q = int(input("Enter prime number q: "))
public_key, private_key = generate_keys(p, q)
print("Public Key:", public_key)
print("Private Key:", private_key)

msg = input("Enter message: ")
encrypted = encrypt(msg, public_key)
print("Encrypted Message:", encrypted)

decrypted = decrypt(encrypted, private_key)
print("Decrypted Message:", decrypted)

## Experiment 6 - Implement Message Authentication and Hashing

In [ ]:
import hashlib
import hmac
import secrets

def sha512_hash(message):
    h = hashlib.sha512(message.encode()).hexdigest()
    return h

def generate_hmac(message, key):
    mac = hmac.new(key.encode(), message.encode(), hashlib.sha512)
    return mac.hexdigest()

def verify_hmac(message, key, mac_value):
    new_mac = hmac.new(key.encode(), message.encode(), hashlib.sha512)
    return hmac.compare_digest(new_mac.hexdigest(), mac_value)

def generate_key(length):
    key = secrets.token_hex(length)
    return key

while True:
    print("\nMAC & Hashing")
    print("1) SHA-512 Hash")
    print("2) Generate HMAC-SHA512")
    print("3) Verify HMAC")
    print("4) Generate Random Key")
    print("q) Quit")
    choice = input("Enter choice: ")
    
    if choice == "1":
        msg = input("Enter message: ")
        print("SHA-512 Hash:", sha512_hash(msg))
    elif choice == "2":
        msg = input("Enter message: ")
        key = input("Enter key: ")
        print("HMAC-SHA512:", generate_hmac(msg, key))
    elif choice == "3":
        msg = input("Enter message: ")
        key = input("Enter key: ")
        mac = input("Enter HMAC value: ")
        result = verify_hmac(msg, key, mac)
        print("HMAC Valid:", result)
    elif choice == "4":
        length = int(input("Enter key length: "))
        print("Generated Key:", generate_key(length))
    elif choice == "q":
        break
    else:
        print("Invalid choice")

## Experiment 7 - Implement Digital Signature

In [ ]:
import hashlib

p = 61
q = 53
n = p * q
phi = (p - 1) * (q - 1)
e = 17

def find_d(e, phi):
    for d in range(1, phi):
        if (e * d) % phi == 1:
            return d

d = find_d(e, phi)
print("Public Key (e, n):", (e, n))
print("Private Key (d, n):", (d, n))

message = input("\nEnter message: ")
hash_value = hashlib.sha256(message.encode()).hexdigest()
hash_int = int(hash_value, 16) % n

print("\nMessage Hash (SHA-256):", hash_value)
print("Hash used for signing (mod n):", hash_int)

# Sign the hash
signature = pow(hash_int, d, n)
print("\nDigital Signature:", signature)

# Verify the signature
verify = pow(signature, e, n)
if verify == hash_int:
    print("\nSignature Verified-->Message is Authentic")
else:
    print("\nSignature Verification Failed-->Message is Tampered")

## Experiment 8 - Authrntication Protocol

In [ ]:
import hashlib
import random

CLIENT_KEY = "secret123"
SERVER_KEY = "secret123"

def hash_value(value, key):
    return hashlib.sha256((str(value) + key).encode()).hexdigest()

def authenticate():
    print("\n--- Authentication Started ---")
    
    # Server challenges Client
    server_challenge = random.randint(1000, 9999)
    print("Server Challenge:", server_challenge)
    
    client_response = hash_value(server_challenge, CLIENT_KEY)
    expected_client = hash_value(server_challenge, SERVER_KEY)
    
    if client_response == expected_client:
        print("Client Authentication: SUCCESS ")
    else:
        print("Client Authentication: FAILED ")
        return

    # Client challenges Server (Mutual Authentication)
    client_challenge = random.randint(1000, 9999)
    print("Client Challenge:", client_challenge)
    
    server_response = hash_value(client_challenge, SERVER_KEY)
    expected_server = hash_value(client_challenge, CLIENT_KEY)
    
    if server_response == expected_server:
        print("Server Authentication: SUCCESS ")
        print("Mutual Authentication: COMPLETED SUCCESSFULLY ")
    else:
        print("Server Authentication: FAILED ")

# Driver Code
print("== Simple Authentication Protocol ==")
message = input("Enter message to authenticate session: ")
authenticate()